In [20]:
import pandas as pd

In [21]:
df = pd.read_csv("data.csv")
df['Timestamp'] = pd.to_datetime(df['Timestamp'], unit='s', utc=True)
df.tail()

Timestamp     Open     High      Low    Close  \
7317754 2025-11-30 23:55:00+00:00  90405.0  90452.0  90403.0  90452.0   
7317755 2025-11-30 23:56:00+00:00  90452.0  90481.0  90420.0  90420.0   
7317756 2025-11-30 23:57:00+00:00  90412.0  90458.0  90396.0  90435.0   
7317757 2025-11-30 23:58:00+00:00  90428.0  90428.0  90362.0  90362.0   
7317758 2025-11-30 23:59:00+00:00  90363.0  90386.0  90362.0  90382.0   

           Volume  
7317754  0.531700  
7317755  0.055547  
7317756  0.301931  
7317757  4.591653  
7317758  0.410369

In [23]:
df['Avg'] = (df['Low'] + df['High']) / 2
df.tail()

Timestamp     Open     High      Low    Close  \
7317754 2025-11-30 23:55:00+00:00  90405.0  90452.0  90403.0  90452.0   
7317755 2025-11-30 23:56:00+00:00  90452.0  90481.0  90420.0  90420.0   
7317756 2025-11-30 23:57:00+00:00  90412.0  90458.0  90396.0  90435.0   
7317757 2025-11-30 23:58:00+00:00  90428.0  90428.0  90362.0  90362.0   
7317758 2025-11-30 23:59:00+00:00  90363.0  90386.0  90362.0  90382.0   

           Volume      Avg  
7317754  0.531700  90427.5  
7317755  0.055547  90450.5  
7317756  0.301931  90427.0  
7317757  4.591653  90395.0  
7317758  0.410369  90374.0

In [25]:
df_days = (
    df.groupby(df["Timestamp"].dt.date)
    .agg(
        Avg=("Avg", "mean"),
        OpenMin=("Open", "min"),
        OpenMax=("Open", "max"),
        CloseMin=("Close", "min"),
        CloseMax=("Close", "max"),
    )
    .reset_index()
)
df_days.tail()

Timestamp           Avg  OpenMin  OpenMax  CloseMin  CloseMax
5078  2025-11-26  88057.301736  86312.0  90574.0   86323.0   90574.0
5079  2025-11-27  91245.092708  90126.0  91888.0   90126.0   91925.0
5080  2025-11-28  91324.308681  90255.0  92970.0   90283.0   92966.0
5081  2025-11-29  90746.479514  90265.0  91158.0   90279.0   91179.0
5082  2025-11-30  91187.356250  90363.0  91940.0   90362.0   91940.0

In [26]:
intervals = []
start_idx = 0
price_base = df_days.loc[start_idx, "Avg"]

for i in range(1, len(df_days)):
    price_now = df_days.loc[i, "Avg"]
    change = abs(price_now - price_base) / price_base

    if change >= 0.10:
        interval = df_days.loc[start_idx:i]
        
        intervals.append({
            "start_date": df_days.loc[start_idx, "Timestamp"],
            "end_date": df_days.loc[i, "Timestamp"],
            "min_open": interval["OpenMin"].min(),
            "max_open": interval["OpenMax"].max(),
            "min_close": interval["CloseMin"].min(),
            "max_close": interval["CloseMax"].max(),
            "start_avg": price_base,
            "end_avg": price_now,
            "change": change,
        })

        start_idx = i + 1
        if start_idx >= len(df_days):
            break
        price_base = df_days.loc[start_idx, "Avg"]

df_intervals = pd.DataFrame(intervals)
df_intervals.tail()

start_date    end_date  min_open  max_open  min_close  max_close  \
316  2025-02-27  2025-04-25   74509.0   95801.0    74515.0    95800.0   
317  2025-04-26  2025-05-11   92877.0  104971.0    92872.0   104965.0   
318  2025-05-12  2025-07-11   98384.0  118833.0    98382.0   118839.0   
319  2025-07-12  2025-11-04   98944.0  126202.0    98943.0   126202.0   
320  2025-11-05  2025-11-18   89291.0  107343.0    89286.0   107343.0   

         start_avg        end_avg    change  
316   85166.063889   94303.907292  0.107294  
317   94500.950347  104182.167708  0.102446  
318  103569.791319  117463.666667  0.134150  
319  117640.026389  103712.985764  0.118387  
320  102514.621181   91705.833333  0.105437